# Etude de la concentration de CO2 dans l'atmosphère depuis 1958

Importation des librairies nécessaires à l'analyse:

In [21]:
%matplotlib inline
import matplotlib.pyplot as plt
import pandas as pd
import isoweek

## Importation des données

Les données sont accessible sur le site de [l'institut Scripps](https://scrippsco2.ucsd.edu/data/atmospheric_co2/primary_mlo_co2_record.html). Elles sont téléchargée en date du 02/06/2021. Si le fichier de données n'a plus de version locale, il sera téléchargé.

In [22]:
data_url = 'https://scrippsco2.ucsd.edu/assets/data/atmospheric/stations/in_situ_co2/monthly/monthly_in_situ_co2_mlo.csv'

data_file = "C02-atmosphere.csv"
import os
import urllib.request
if not os.path.exists(data_file):
    urllib.request.urlretrieve(data_url, data_file)

Les 54 premières lignes du fichiers sont une description des données et quelques indications, elle ne seront pas prise en compte lors de la création du dataFrame de l'analyse.  
La structure des données, comme indiquée dans le fichier CSV est la suivante:  

| Nom de colonne | Libellé de colonne                                                                                                                |
|----------------|-----------------------------------------------------------------------------------------------------------------------------------|
| Year           | Année aucours de laquelle la mesure a été faite                                                                                 |
| Month          | Mois au cours duquel la mesure a été faite
                    |
| Date           | Date de la mesure au format Excel
                    |
| Date           | Date de la mesure au format ISO
                    |
| CO2 (ppm)      | Taux de CO2 en micro mole par mole (ppm)
                    |
| CO2 adjusted (ppm)| Taux de CO2 auquel on a retiré les variations saisonnières
                    |
| CO2 smoothed(ppm) | Taux de CO2 ajusté
                    |
| CO2 smoothed and adjusted (ppm) | Taux de CO2 auquel on a retiré les variations saisonnières et ajusté
                    |
| CO2 completed (ppm) | Identique à la colonne 5, les valeurs manquantes sont prises dans la colonne 7
                    |
| CO2 adjusted completed (ppm) | Identique à la colonne 6, les valeurs manquantes sont prises dans la colonne 8
                    |  
                    
 

In [23]:
raw_data = pd.read_csv(data_file, skiprows=54)
raw_data.head()

Yr   Mn      Date        Date        CO2  seasonally          fit  \
0                                                adjusted                
1                Excel                  [ppm]      [ppm]         [ppm]   
2  1958   01     21200   1958.0411     -99.99      -99.99       -99.99   
3  1958   02     21231   1958.1260     -99.99      -99.99       -99.99   
4  1958   03     21259   1958.2027     315.70      314.44       316.19   

     seasonally           CO2       seasonally  
0  adjusted fit        filled  adjusted filled  
1         [ppm]         [ppm]            [ppm]  
2        -99.99        -99.99           -99.99  
3        -99.99        -99.99           -99.99  
4        314.91        315.70           314.44

Les lignes 0 et 1 vont gêner l'analyse et ne contiennent que des indications sur les données. Nous les retirons:

In [24]:
data = raw_data.drop(labels=[0,1], axis=0).copy()
data.head()

Yr   Mn      Date        Date        CO2 seasonally          fit  \
2  1958   01     21200   1958.0411     -99.99     -99.99       -99.99   
3  1958   02     21231   1958.1260     -99.99     -99.99       -99.99   
4  1958   03     21259   1958.2027     315.70     314.44       316.19   
5  1958   04     21290   1958.2877     317.45     315.16       317.30   
6  1958   05     21320   1958.3699     317.51     314.70       317.87   

    seasonally          CO2  seasonally  
2       -99.99       -99.99      -99.99  
3       -99.99       -99.99      -99.99  
4       314.91       315.70      314.44  
5       314.99       317.45      315.16  
6       315.07       317.51      314.70

Les titres de colonnes contiennent des espaces qui gêne leur appel. Nous renommons donc les colonnes comme suit:

In [25]:
col_list = data.columns
data.rename(columns={col_list[0]: 'year', col_list[1]: 'month', col_list[2]: 'Date1',
                     col_list[3]: 'Date2', col_list[4]: 'CO2', col_list[5]: 'CO2 overall',
                    col_list[6]: 'C02_3', col_list[7]: 'CO2_4', col_list[8]: 'C02_5',
                    col_list[9]: 'CO2_6'}, inplace=True)
data.head()


year month     Date1       Date2        CO2 CO2 overall        C02_3  \
2  1958    01     21200   1958.0411     -99.99      -99.99       -99.99   
3  1958    02     21231   1958.1260     -99.99      -99.99       -99.99   
4  1958    03     21259   1958.2027     315.70      314.44       316.19   
5  1958    04     21290   1958.2877     317.45      315.16       317.30   
6  1958    05     21320   1958.3699     317.51      314.70       317.87   

       CO2_4        C02_5      CO2_6  
2     -99.99       -99.99     -99.99  
3     -99.99       -99.99     -99.99  
4     314.91       315.70     314.44  
5     314.99       317.45     315.16  
6     315.07       317.51     314.70

On converti les colonnes 'year' et 'month' en période que l'on défini ensuite comme index

In [26]:
def convert_month(year,month):
    return pd.Period(year = int(year), month = int(month), freq='M')

data['period'] = [convert_month(year,month) for year,month in zip(data['year'],data['month'])]
data = data.set_index('period')
data.head()

year month     Date1       Date2        CO2 CO2 overall        C02_3  \
period                                                                          
1958-01  1958    01     21200   1958.0411     -99.99      -99.99       -99.99   
1958-02  1958    02     21231   1958.1260     -99.99      -99.99       -99.99   
1958-03  1958    03     21259   1958.2027     315.70      314.44       316.19   
1958-04  1958    04     21290   1958.2877     317.45      315.16       317.30   
1958-05  1958    05     21320   1958.3699     317.51      314.70       317.87   

             CO2_4        C02_5      CO2_6  
period                                      
1958-01     -99.99       -99.99     -99.99  
1958-02     -99.99       -99.99     -99.99  
1958-03     314.91       315.70     314.44  
1958-04     314.99       317.45     315.16  
1958-05     315.07       317.51     314.70

On vérifie qu'il n'y a pas de trou dans les périodes:

In [ ]:
periods = data.index
for p1, p2 in zip(periods[:-1], periods[1:]):
    delta = p2.to_timestamp() - p1.end_time
    if delta > pd.Timedelta('1s'):
        print(p1, p2)

-99.99